# Обрабатываем сорс-данные и вставляем их в SQL-базу

Вся аналитика по данному дата-сету будет произведена в SQL

**1. Читаем файл с данными о видеоиграх и записываем его содержимое в переменную file_content**

In [94]:
import csv

file_content = []

with open("./Source_data/vgsales.csv", encoding="utf-8") as f:
    reader = csv.reader(f)
    for row in reader:
        for cell in row:
            try:
                row[row.index(cell)] = int(cell)
            except:
                try:
                    row[row.index(cell)] = float(cell)
                except:
                    ##Если значение содержит "N/A", в сорсе у этой клетки отсутствуют данные по году выпуска
                    ##Если у строки есть одинарная кавычка, заменим ее на двойную, чтобы не нарушать синтаксис SQL-запроса
                    if str(cell) == 'N/A':
                        row[row.index(cell)] = int()
                    else:
                        row[row.index(cell)] = cell[0:100].replace("'","''")
        file_content.append(row)

**2. Открываем коннекшн с базой данных.**

Задача: Создать таблицу, которая будет соответствовать данным, полученным из файла и запихнуть туда эти данные.

In [106]:
import pyodbc as db

try:
    conn = db.connect(
    "Driver=SQL Server Native Client 11.0;"
    "Server=DESKTOP-D4KA4D1\SQLEXPRESS;"
    "Database=master;"
    "Trusted_Connection=yes;",
    autocommit=True)
    
    cursor = conn.cursor()
    print("Connected successfully")
    
except:
    print("Connection failed. Check code.")

Connected successfully


**3. Проверяем, создана ли база и таблица. Если не создана, создаем.**

In [108]:
try:
    cursor.execute("use AnalysisDB")
    print("Database already created")
except:
    cursor.execute("create database AnalysisDB")
    conn.commit()
    cursor.execute("use AnalysisDB")
    print("Created database")

try:
    cursor.execute("select * from Videogames_data")
    print("Table already created")
except:
    cursor.execute(
        """
        create table Videogames_data
               (
                   Rank Int Primary Key,
                   Name varchar(100),
                   Platform varchar(100),
                   Year Int,
                   Genre varchar(100),
                   Publisher varchar(100),
                   NA_Sales float,
                   EU_Sales float,
                   JP_Sales float,
                   Other_Sales float,
                   Global_Sales float
               )
        """
    )
    conn.commit()
    print("Created table")

Database already created
Table already created


In [109]:
for row in file_content:
    print(row)

['Rank', 'Name', 'Platform', 'Year', 'Genre', 'Publisher', 'NA_Sales', 'EU_Sales', 'JP_Sales', 'Other_Sales', 'Global_Sales']
[1, 'Wii Sports', 'Wii', 2006, 'Sports', 'Nintendo', 41.49, 29.02, 3.77, 8.46, 82.74]
[2, 'Super Mario Bros.', 'NES', 1985, 'Platform', 'Nintendo', 29.08, 3.58, 6.81, 0.77, 40.24]
[3, 'Mario Kart Wii', 'Wii', 2008, 'Racing', 'Nintendo', 15.85, 12.88, 3.79, 3.31, 35.82]
[4, 'Wii Sports Resort', 'Wii', 2009, 'Sports', 'Nintendo', 15.75, 11.01, 3.28, 2.96, 33]
[5, 'Pokemon Red/Pokemon Blue', 'GB', 1996, 'Role-Playing', 'Nintendo', 11.27, 8.89, 10.22, 1, 31.37]
[6, 'Tetris', 'GB', 1989, 'Puzzle', 'Nintendo', 23.2, 2.26, 4.22, 0.58, 30.26]
[7, 'New Super Mario Bros.', 'DS', 2006, 'Platform', 'Nintendo', 11.38, 9.23, 6.5, 2.9, 30.01]
[8, 'Wii Play', 'Wii', 2006, 'Misc', 'Nintendo', 14.03, 9.2, 2.93, 2.85, 29.02]
[9, 'New Super Mario Bros. Wii', 'Wii', 2009, 'Platform', 'Nintendo', 14.59, 7.06, 4.7, 2.26, 28.62]
[10, 'Duck Hunt', 'NES', 1984, 'Shooter', 'Nintendo', 26.

[1848, 'Toy Story 3: The Video Game', 'PS3', 2010, 'Action', 'Disney Interactive Studios', 0.51, 0.42, 0, 0.17, 1.11]
[1849, 'Guitar Hero 5', 'PS3', 2009, 'Misc', 'Activision', 0.53, 0.4, 0, 0.17, 1.1]
[1850, 'Megamania', 2600, 1981, 'Shooter', 'Activision', 1.03, 0.06, 0, 0.01, 1.1]
[1851, 'Medal of Honor: Airborne', 'X360', 2007, 'Shooter', 'Electronic Arts', 0.45, 0.53, 0.01, 0.12, 1.1]
[1852, 'The Legend of Zelda: Tri Force Heroes', '3DS', 2015, 'Action', 'Nintendo', 0.52, 0.33, 0.17, 0.08, 1.1]
[1853, 'Jungle Hunt', 2600, 1982, 'Platform', 'Atari', 1.03, 0.06, 0, 0.01, 1.1]
[1854, 'Triple Play 98', 'PS', 1997, 'Sports', 'Electronic Arts', 0.61, 0.42, 0, 0.07, 1.1]
[1855, 'LEGO The Lord of the Rings', 'PS3', 2012, 'Action', 'Warner Bros. Interactive Entertainment', 0.36, 0.53, 0, 0.21, 1.1]
[1856, 'Petz Dogz 2', 'DS', 2007, 'Simulation', 'Ubisoft', 0.47, 0.52, 0, 0.12, 1.1]
[1857, 'WWE SmackDown vs. Raw 2011', 'PS3', 2010, 'Fighting', 'THQ', 0.44, 0.46, 0.01, 0.18, 1.1]
[1858, 'Yu-

[4315, 'Missile Command', 'PS', 1999, 'Shooter', 'Atari', 0.25, 0.17, 0, 0.03, 0.45]
[4316, 'Lego Batman 3: Beyond Gotham', '3DS', 2014, 'Action', 'Warner Bros. Interactive Entertainment', 0.21, 0.21, 0, 0.04, 0.45]
[4317, 'Barbie as The Island Princess', 'Wii', 2007, 'Adventure', 'Activision', 0.42, 0, 0, 0.03, 0.45]
[4318, 'Jikkyou Powerful Pro Yakyuu 3', 'SNES', 1996, 'Sports', 'Konami Digital Entertainment', 0, 0, 0.45, 0, 0.45]
[4319, 'The Walking Dead: Season One', 'PS4', 2014, 'Adventure', 'Telltale Games', 0.12, 0.25, 0.01, 0.08, 0.45]
[4320, 'Jikkyou Powerful Pro Yakyuu 12', 'PS2', 2005, 'Sports', 'Konami Digital Entertainment', 0, 0, 0.45, 0, 0.45]
[4321, 'Enter the Matrix', 'GC', 2003, 'Action', 'Atari', 0.34, 0.09, 0.02, 0.01, 0.45]
[4322, 'Crash: Mind Over Mutant', 'Wii', 2008, 'Platform', 'Vivendi Games', 0.36, 0.06, 0, 0.03, 0.45]
[4323, 'NASCAR 2005: Chase for the Cup', 'XB', 2004, 'Racing', 'Electronic Arts', 0.34, 0.1, 0, 0.02, 0.45]
[4324, "J-League Excite Stage ''95

[6076, 'Looney Tunes Racing', 'PS', 2000, 'Racing', 'Infogrames', 0.16, 0.11, 0, 0.02, 0.29]
[6077, 'Final Fantasy X-2: International + Last Mission', 'PS2', 2004, 'Role-Playing', 'Square Enix', 0, 0, 0.29, 0, 0.29]
[6078, 'Namco Museum Vol.2', 'PS', 1996, 'Misc', 'Sony Computer Entertainment', 0.03, 0.02, 0.21, 0.02, 0.29]
[6079, 'Rayman 3: Hoodlum Havoc', 'PS2', 2003, 'Platform', 'Ubisoft', 0.14, 0.11, 0, 0.04, 0.29]
[6080, "Penguin no Mondai: Saikyou Penguin Densetsu! A Penguin''s Troubles", 'DS', 2008, 'Adventure', 'Konami Digital Entertainment', 0, 0, 0.29, 0, 0.29]
[6081, 'Psi-Ops: The Mindgate Conspiracy', 'PS2', 2004, 'Shooter', 'Midway Games', 0.14, 0.11, 0, 0.04, 0.29]
[6082, 'I Spy: Spooky Mansion', 'Wii', 2010, 'Puzzle', 'Storm City Games', 0.27, 0, 0, 0.02, 0.29]
[6083, 'Tomba! 2: The Evil Swine Return', 'PS', 1999, 'Platform', 'Sony Computer Entertainment', 0.16, 0.11, 0, 0.02, 0.29]
[6084, 'SAW', 'X360', 2009, 'Action', 'Konami Digital Entertainment', 0.13, 0.12, 0, 0.03

[8419, 'WRC 2: FIA World Rally Championship', 'PS3', 2011, 'Racing', 'Ubisoft', 0, 0.13, 0, 0.04, 0.17]
[8420, 'Blood Bowl', 'X360', 2009, 'Sports', 'Focus Home Interactive', 0.13, 0.03, 0, 0.01, 0.17]
[8421, 'Matchbox Cross Town Heroes', 'GBA', 2002, 'Racing', 'THQ', 0.12, 0.04, 0, 0, 0.17]
[8422, 'Wolfenstein 3D', 'GBA', 2002, 'Shooter', 'BAM! Entertainment', 0.12, 0.04, 0, 0, 0.17]
[8423, 'Nobunaga no Yabou: Tenshoki', 'SNES', 1996, 'Strategy', 'Tecmo Koei', 0, 0, 0.17, 0, 0.17]
[8424, 'Learning to Spell', 'DS', 2010, 'Misc', '505 Games', 0.16, 0, 0, 0.01, 0.17]
[8425, 'Go, Diego, Go! Safari Rescue', 'DS', 2007, 'Adventure', 'Take-Two Interactive', 0.15, 0.01, 0, 0.01, 0.17]
[8426, 'Super Power League', 'SNES', 1993, 'Sports', 'Hudson Soft', 0, 0, 0.17, 0, 0.17]
[8427, 'Easy Piano', 'DS', 2009, 'Misc', 'Game Life', 0.04, 0.11, 0, 0.02, 0.17]
[8428, 'Street Fighter Alpha 2', 'SNES', 1996, 'Fighting', 'Nintendo', 0, 0, 0.17, 0, 0.17]
[8429, 'Dragon Quest X', '3DS', 2014, 'Role-Playing

[10419, 'Winning Eleven: Pro Evolution Soccer 2007', 'X360', 2006, 'Sports', 'Konami Digital Entertainment', 0.09, 0, 0, 0.01, 0.1]
[10420, 'Ennichi no Tatsujin', 'Wii', 2006, 'Misc', 'Namco Bandai Games', 0, 0, 0.1, 0, 0.1]
[10421, 'Squinkies 2: Adventure Mall Surprize!', 'DS', 2011, 'Platform', 'Activision', 0.1, 0, 0, 0.01, 0.1]
[10422, 'Wizardry VI: Bane of the Cosmic Forge', 'SNES', 1995, 'Role-Playing', 'ASCII Entertainment', 0, 0, 0.1, 0, 0.1]
[10423, 'Power Pocket Koushien', 'DS', 2005, 'Sports', 'Konami Digital Entertainment', 0, 0, 0.1, 0, 0.1]
[10424, 'Gravity Games Bike: Street Vert Dirt', 'PS2', 2002, 'Sports', 'Midway Games', 0.05, 0.04, 0, 0.01, 0.1]
[10425, 'Contact', 'DS', 2006, 'Role-Playing', 'Rising Star Games', 0.07, 0, 0.03, 0.01, 0.1]
[10426, 'Pro Yaky? Spirits 2010', 'PS2', 2010, 'Sports', 'Konami Digital Entertainment', 0, 0, 0.1, 0, 0.1]
[10427, 'Princess Debut', 'DS', 2008, 'Misc', 'Cave', 0.1, 0, 0, 0.01, 0.1]
[10428, 'My First Dollhouse', 'DS', 2010, 'Misc'

[12418, 'MotoGP 10/11', 'X360', 2011, 'Racing', 'Capcom', 0, 0.05, 0, 0.01, 0.06]
[12419, 'Alone in the Dark', 'PS2', 2008, 'Adventure', 'Atari', 0.03, 0.02, 0, 0.01, 0.06]
[12420, 'Guilty Gear XX Accent Core Plus', 'PS2', 2008, 'Fighting', 'PQube', 0.03, 0.02, 0, 0.01, 0.06]
[12421, 'Muppets Party Cruise', 'PS2', 2003, 'Misc', 'TDK Mediactive', 0.03, 0.02, 0, 0.01, 0.06]
[12422, 'Higurashi Daybreak Portable', 'PSP', 2008, 'Adventure', 'Alchemist', 0, 0, 0.06, 0, 0.06]
[12423, 'Crayon Shin-chan: Arashi o Yobu Kasukabe Eiga Stars!', '3DS', 2014, 'Adventure', 'Namco Bandai Games', 0, 0, 0.06, 0, 0.06]
[12424, "Shonen Jump''s One Piece: Grand Battle", 'GC', 2005, 'Fighting', 'Namco Bandai Games', 0.05, 0.01, 0, 0, 0.06]
[12425, 'Barbie Horse Adventures: Wild Horse Rescue', 'XB', 2003, 'Sports', 'Vivendi Games', 0.05, 0.01, 0, 0, 0.06]
[12426, 'Winx Club: Quest for the Codex', 'DS', 2006, 'Action', 'Konami Digital Entertainment', 0.03, 0.02, 0, 0.01, 0.06]
[12427, 'Blast Lacrosse', 'PS', 2

[14419, 'Puzzle & Action: Tant-R', 'GEN', 1994, 'Misc', 'Sega', 0, 0, 0.03, 0, 0.03]
[14420, 'Code Lyoko: Quest for Infinity', 'PSP', 2008, 'Action', 'Game Factory', 0.03, 0, 0, 0, 0.03]
[14421, 'Away: Shuffle Dungeon', 'DS', 2008, 'Role-Playing', 'Majesco Entertainment', 0.02, 0, 0, 0, 0.03]
[14422, 'Digimon World 4', 'XB', 2005, 'Role-Playing', 'Atari', 0.02, 0.01, 0, 0, 0.03]
[14423, 'Bubble Bobble Evolution', 'PSP', 2006, 'Puzzle', 'Rising Star Games', 0.03, 0, 0, 0, 0.03]
[14424, 'Codename: Panzers Cold War', 'PC', 2009, 'Strategy', 'Atari', 0, 0.02, 0, 0.01, 0.03]
[14425, 'Kekkaishi: Kokubourou Shuurai', 'DS', 2008, 'Action', 'Namco Bandai Games', 0, 0, 0.03, 0, 0.03]
[14426, 'Shugo Chara! Amunonijiro Chara Change', 'DS', 2008, 'Action', 'Konami Digital Entertainment', 0, 0, 0.03, 0, 0.03]
[14427, 'Galleon: Islands of Mystery', 'XB', 2004, 'Action', 'SCi', 0.02, 0.01, 0, 0, 0.03]
[14428, 'Renai 0 Kilometer', 'PSP', 2013, 'Adventure', 'Alchemist', 0, 0, 0.03, 0, 0.03]
[14429, 'Wor

[15937, 'Katekyoo Hitman Reborn! DS: Mafia Daishuugou Bongole Festival', 'DS', 2008, 'Action', 'Takara Tomy', 0, 0, 0.02, 0, 0.02]
[15938, 'Pippa Funnell 2: Farm Adventures', 'DS', 2007, 'Simulation', 'Ubisoft', 0, 0.01, 0, 0, 0.02]
[15939, 'Iron Soldier 3', 'PS', 1999, 'Simulation', 'Telegames', 0.01, 0.01, 0, 0, 0.02]
[15940, 'Oyaku de Asoberu DS Ehon: Ukkari Penelope', 'DS', 2008, 'Simulation', 'Tecmo Koei', 0, 0, 0.02, 0, 0.02]
[15941, 'Space Invaders Revolution', 'DS', 2005, 'Shooter', 'Rising Star Games', 0.01, 0, 0, 0, 0.02]
[15942, 'Barbie and Her Sisters Puppy Rescue', 'PS3', 2015, 'Action', 'Namco Bandai Games', 0, 0.01, 0, 0, 0.02]
[15943, 'Worms: WMD', 'PS4', 2016, 'Action', 'Sold Out', 0.01, 0.01, 0, 0, 0.02]
[15944, 'Myst', 'PSP', 2006, 'Adventure', 'Midway Games', 0, 0.01, 0, 0, 0.02]
[15945, 'UNO 52', 'DS', 2006, 'Misc', 'Zoo Digital Publishing', 0.01, 0, 0, 0, 0.02]
[15946, "Tiger & Bunny: Hero''s Day", 'PSP', 2013, 'Action', 'D3Publisher', 0, 0, 0.02, 0, 0.02]
[15947,

**4. Инсертим данные в таблицу**

И дополнительно создаем файл .sql, который будет содержать код инсертов

In [111]:
with open("videogames_data.sql", "w", encoding="utf-8") as file:
        cursor.execute("delete from Videogames_data")
        for row in file_content[1:]:
            data_string = ""
            for cell in row:
                if type(cell) == str:
                    data_string += "'"+str(cell)+"'" + ","
                else:
                    data_string += str(cell) + ","
            data_string = data_string[0:-1]
            print("insert into Videogames_data values({0});".format(data_string))
            file.write("insert into Videogames_data values({0});\n".format(data_string))
            try:
                cursor.execute("insert into Videogames_data values({0});".format(data_string))
            except:
                raise
                break

conn.commit()

insert into Videogames_data values(1,'Wii Sports','Wii',2006,'Sports','Nintendo',41.49,29.02,3.77,8.46,82.74);
insert into Videogames_data values(2,'Super Mario Bros.','NES',1985,'Platform','Nintendo',29.08,3.58,6.81,0.77,40.24);
insert into Videogames_data values(3,'Mario Kart Wii','Wii',2008,'Racing','Nintendo',15.85,12.88,3.79,3.31,35.82);
insert into Videogames_data values(4,'Wii Sports Resort','Wii',2009,'Sports','Nintendo',15.75,11.01,3.28,2.96,33);
insert into Videogames_data values(5,'Pokemon Red/Pokemon Blue','GB',1996,'Role-Playing','Nintendo',11.27,8.89,10.22,1,31.37);
insert into Videogames_data values(6,'Tetris','GB',1989,'Puzzle','Nintendo',23.2,2.26,4.22,0.58,30.26);
insert into Videogames_data values(7,'New Super Mario Bros.','DS',2006,'Platform','Nintendo',11.38,9.23,6.5,2.9,30.01);
insert into Videogames_data values(8,'Wii Play','Wii',2006,'Misc','Nintendo',14.03,9.2,2.93,2.85,29.02);
insert into Videogames_data values(9,'New Super Mario Bros. Wii','Wii',2009,'Platfor

insert into Videogames_data values(308,'Assassin''s Creed IV: Black Flag','PS3',2013,'Action','Ubisoft',1.33,1.71,0.13,0.73,3.89);
insert into Videogames_data values(309,'Monster Hunter 4 Ultimate','3DS',2014,'Role-Playing','Nintendo',0.67,0.49,2.62,0.11,3.89);
insert into Videogames_data values(310,'MotorStorm','PS3',2006,'Racing','Sony Computer Entertainment',1.53,1.61,0.06,0.67,3.88);
insert into Videogames_data values(311,'The Elder Scrolls V: Skyrim','PC',2011,'Role-Playing','Bethesda Softworks',1.15,2.09,0,0.64,3.88);
insert into Videogames_data values(312,'Tekken 5','PS2',2005,'Fighting','Namco Bandai Games',0.93,1.94,0.31,0.7,3.87);
insert into Videogames_data values(313,'Dragon Warrior III','NES',1988,'Role-Playing','Enix Corporation',0.1,0,3.77,0,3.87);
insert into Videogames_data values(314,'Sports Champions','PS3',2010,'Sports','Sony Computer Entertainment',2.12,1.14,0.1,0.51,3.87);
insert into Videogames_data values(315,'NBA 2K16','PS4',2015,'Sports','Take-Two Interactive'

insert into Videogames_data values(527,'Yoshi''s Island DS','DS',2006,'Platform','Nintendo',1.47,0.07,1.1,0.15,2.8);
insert into Videogames_data values(528,'Hot Shots Golf','PS',1997,'Sports','Sony Computer Entertainment',0.29,0.2,2.13,0.18,2.79);
insert into Videogames_data values(529,'Killzone 3','PS3',2011,'Shooter','Sony Computer Entertainment',1.45,0.88,0.09,0.38,2.79);
insert into Videogames_data values(530,'A Bug''s Life','PS',1998,'Platform','Sony Computer Entertainment',1.96,0.72,0,0.11,2.79);
insert into Videogames_data values(531,'WWF SmackDown! Just Bring It','PS2',2001,'Fighting','THQ',1.19,1.15,0.04,0.41,2.79);
insert into Videogames_data values(532,'Dragon Quest V: Tenkuu no Hanayome','SNES',1992,'Role-Playing','Enix Corporation',0,0,2.78,0.01,2.79);
insert into Videogames_data values(533,'Mortal Kombat Trilogy','PS',1996,'Fighting','GT Interactive',1.98,0.7,0,0.11,2.79);
insert into Videogames_data values(534,'Battlefield 3','PC',2011,'Shooter','Electronic Arts',0.89,1.

insert into Videogames_data values(731,'Need for Speed: Hot Pursuit','X360',2010,'Racing','Electronic Arts',1.03,0.98,0,0.21,2.22);
insert into Videogames_data values(732,'BioShock 2','X360',2010,'Shooter','Take-Two Interactive',1.45,0.55,0.02,0.19,2.21);
insert into Videogames_data values(733,'Assassin''s Creed IV: Black Flag','XOne',2013,'Action','Ubisoft',1.47,0.55,0,0.19,2.21);
insert into Videogames_data values(734,'Devil May Cry 3: Dante''s Awakening Special Edition','PS2',2006,'Action','Capcom',1.06,0.82,0.05,0.28,2.21);
insert into Videogames_data values(735,'Rock Band 2','X360',2008,'Misc','Electronic Arts',1.78,0.24,0,0.18,2.2);
insert into Videogames_data values(736,'Frogger',2600,1981,'Action','Parker Bros.',2.06,0.12,0,0.02,2.2);
insert into Videogames_data values(737,'Guitar Hero II','X360',2007,'Misc','Activision',2.01,0.02,0,0.17,2.2);
insert into Videogames_data values(738,'Wario Land 3','GB',2000,'Platform','Nintendo',1.11,0.51,0.34,0.23,2.2);
insert into Videogames_d

insert into Videogames_data values(974,'Dragon Quest Monsters: Joker','DS',2006,'Role-Playing','Square Enix',0.23,0.03,1.49,0.03,1.78);
insert into Videogames_data values(975,'SpongeBob SquarePants: SuperSponge','PS',2001,'Action','THQ',1.12,0.58,0,0.08,1.78);
insert into Videogames_data values(976,'The Getaway: Black Monday','PS2',2004,'Action','Sony Computer Entertainment',0.39,1.01,0.02,0.36,1.78);
insert into Videogames_data values(977,'Professor Layton and the Mask of Miracle','3DS',2011,'Puzzle','Nintendo',0.32,0.95,0.36,0.14,1.78);
insert into Videogames_data values(978,'Just Cause 2','PS3',2010,'Action','Square Enix',0.45,0.94,0.06,0.33,1.78);
insert into Videogames_data values(979,'Dragon''s Dogma','PS3',2012,'Role-Playing','Capcom',0.41,0.46,0.72,0.19,1.78);
insert into Videogames_data values(980,'The Legend of Zelda: The Wind Waker','WiiU',2013,'Action','Nintendo',0.93,0.57,0.14,0.13,1.77);
insert into Videogames_data values(981,'50 Cent: Bulletproof','PS2',2005,'Action','Vi

...

insert into Videogames_data values(15386,'Samurai & Dragons','PSV',2012,'Action','Sega',0,0,0.02,0,0.02);
insert into Videogames_data values(15387,'TV Anime Idolm@ster: Cinderella Girls G4U! Pack Vol.7','PS3',2015,'Misc','Namco Bandai Games',0,0,0.02,0,0.02);
insert into Videogames_data values(15388,'Elminage Original: Majo to Megami to Kamigami no Yubiwa','PSP',2011,'Role-Playing','Starfish',0,0,0.02,0,0.02);
insert into Videogames_data values(15389,'TalkMan','PSP',2006,'Misc','Sony Computer Entertainment',0,0,0.02,0,0.02);
insert into Videogames_data values(15390,'XGRA: Extreme G Racing Association','XB',2003,'Racing','Acclaim Entertainment',0.02,0,0,0,0.02);
insert into Videogames_data values(15391,'Uta no * Prince-Sama','PSP',2010,'Adventure','Broccoli',0,0,0.02,0,0.02);
insert into Videogames_data values(15392,'Ridge Racer Unbounded','PC',2012,'Racing','Namco Bandai Games',0,0.02,0,0,0.02);
insert into Videogames_data values(15393,'Elminage Gothic: Ulm Zakir to Yami no Gishiki','P

insert into Videogames_data values(15648,'PDC World Championship Darts 2009','Wii',2009,'Sports','Oxygen Interactive',0,0.02,0,0,0.02);
insert into Videogames_data values(15649,'Tour de France 2014','PS3',2014,'Sports','Focus Home Interactive',0,0.02,0,0,0.02);
insert into Videogames_data values(15650,'The Hustle: Detroit Streets','XB',2006,'Sports','Activision',0.01,0,0,0,0.02);
insert into Videogames_data values(15651,'Tail of the Sun','PS',1996,'Role-Playing','ArtDink',0.01,0.01,0,0,0.02);
insert into Videogames_data values(15652,'Canada Hunt','Wii',2010,'Sports','Virtual Play Games',0.02,0,0,0,0.02);
insert into Videogames_data values(15653,'Space Channel 5: Ulala''s Cosmic Attack','GBA',2002,'Misc','Atari',0.01,0,0,0,0.02);
insert into Videogames_data values(15654,'Airline Tycoon','PC',2000,'Simulation','Interplay',0,0.01,0,0,0.02);
insert into Videogames_data values(15655,'Virtua Quest','PS2',0,'Role-Playing','Unknown',0.01,0.01,0,0,0.02);
insert into Videogames_data values(15656

insert into Videogames_data values(15928,'Professional Farmer 2016','PS4',2015,'Action','Namco Bandai Games',0,0.01,0,0,0.02);
insert into Videogames_data values(15929,'Storm Lover Kai!!','PSP',2012,'Action','D3Publisher',0,0,0.02,0,0.02);
insert into Videogames_data values(15930,'Race Driver: Create & Race','DS',2007,'Racing','Codemasters',0.01,0,0,0,0.02);
insert into Videogames_data values(15931,'Nurarihyon no Mago: Hyakki Ryouran Taisen','PS3',2011,'Fighting','Konami Digital Entertainment',0,0,0.02,0,0.02);
insert into Videogames_data values(15932,'Minna to Issho','PSV',2011,'Misc','Sony Computer Entertainment',0,0,0.02,0,0.02);
insert into Videogames_data values(15933,'Harukanaru Toki no Naka de 6','PSP',2015,'Action','Tecmo Koei',0,0,0.02,0,0.02);
insert into Videogames_data values(15934,'Hummer Badlands','XB',2006,'Racing','Global Star',0.01,0,0,0,0.02);
insert into Videogames_data values(15935,'I Doll U','PSV',2015,'Adventure','Idea Factory',0,0,0.02,0,0.02);
insert into Videog

insert into Videogames_data values(16191,'Toro to Morimori','PS3',2009,'Misc','Sony Computer Entertainment',0,0,0.01,0,0.01);
insert into Videogames_data values(16192,'Sonic & All-Stars Racing Transformed','PC',2013,'Racing','Sega',0,0.01,0,0,0.01);
insert into Videogames_data values(16193,'Satisfashion','Wii',2010,'Misc','Destineer',0.01,0,0,0,0.01);
insert into Videogames_data values(16194,'Homeworld Remastered Collection','PC',0,'Strategy',0,0,0.01,0,0,0.01);
insert into Videogames_data values(16195,'Metal Slug Anthology','PS2',2007,'Shooter','Ignition Entertainment',0,0,0.01,0,0.01);
insert into Videogames_data values(16196,'K-1 Grand Prix','PS',1999,'Fighting','Jaleco',0.01,0.01,0,0,0.01);
insert into Videogames_data values(16197,'Shorts','DS',0,'Platform','Unknown',0.01,0,0,0,0.01);
insert into Videogames_data values(16198,'Legoland','PC',1999,'Action','LEGO Media',0,0.01,0,0,0.01);
insert into Videogames_data values(16199,'Rave Master: Special Attack Force!','GBA',2002,'Fighting

insert into Videogames_data values(16485,'Dragon Ball Z for Kinect','X360',2012,'Fighting','Namco Bandai Games',0.01,0,0,0,0.01);
insert into Videogames_data values(16486,'Hospital Tycoon','PC',2007,'Strategy','Codemasters',0,0.01,0,0,0.01);
insert into Videogames_data values(16487,'Smart Boy''s Winter Wonderland','DS',2008,'Misc','UFO Interactive',0.01,0,0,0,0.01);
insert into Videogames_data values(16488,'Koi Sentai Love & Peace the P.S.P: Power Zenkai! Special Youso Tenkomori de Portable Ka Daisakusen d','PSP',2012,'Action','Broccoli',0,0,0.01,0,0.01);
insert into Videogames_data values(16489,'Case Closed: One Truth Prevails','Wii',2007,'Adventure','Nobilis',0,0,0.01,0,0.01);
insert into Videogames_data values(16490,'Slotter Mania P: Tetsuya Shinjuku vs Ueno','PSP',2010,'Misc','Dorart',0,0,0.01,0,0.01);
insert into Videogames_data values(16491,'Bomberman','Wii',2008,'Puzzle','Hudson Entertainment',0,0,0.01,0,0.01);
insert into Videogames_data values(16492,'Micro Machines V4','PS2',2

**5. Проверяем, записались ли данные, затем закрываем коннекшн**

In [112]:
cursor.execute("select * from Videogames_data")
for row in cursor:
    print(row)
    
conn.close()

(1, 'Wii Sports', 'Wii', 2006, 'Sports', 'Nintendo', 41.49, 29.02, 3.77, 8.46, 82.74)
(2, 'Super Mario Bros.', 'NES', 1985, 'Platform', 'Nintendo', 29.08, 3.58, 6.81, 0.77, 40.24)
(3, 'Mario Kart Wii', 'Wii', 2008, 'Racing', 'Nintendo', 15.85, 12.88, 3.79, 3.31, 35.82)
(4, 'Wii Sports Resort', 'Wii', 2009, 'Sports', 'Nintendo', 15.75, 11.01, 3.28, 2.96, 33.0)
(5, 'Pokemon Red/Pokemon Blue', 'GB', 1996, 'Role-Playing', 'Nintendo', 11.27, 8.89, 10.22, 1.0, 31.37)
(6, 'Tetris', 'GB', 1989, 'Puzzle', 'Nintendo', 23.2, 2.26, 4.22, 0.58, 30.26)
(7, 'New Super Mario Bros.', 'DS', 2006, 'Platform', 'Nintendo', 11.38, 9.23, 6.5, 2.9, 30.01)
(8, 'Wii Play', 'Wii', 2006, 'Misc', 'Nintendo', 14.03, 9.2, 2.93, 2.85, 29.02)
(9, 'New Super Mario Bros. Wii', 'Wii', 2009, 'Platform', 'Nintendo', 14.59, 7.06, 4.7, 2.26, 28.62)
(10, 'Duck Hunt', 'NES', 1984, 'Shooter', 'Nintendo', 26.93, 0.63, 0.28, 0.47, 28.31)
(11, 'Nintendogs', 'DS', 2005, 'Simulation', 'Nintendo', 9.07, 11.0, 1.93, 2.75, 24.76)
(12, 

(810, 'Spec Ops: Airborne Commando', 'PS', 2002, 'Shooter', 'Take-Two Interactive', 1.54, 0.46, 0.0, 0.08, 2.07)
(811, 'Kingdom Hearts: Birth by Sleep', 'PSP', 2010, 'Role-Playing', 'Square Enix', 0.63, 0.42, 0.75, 0.26, 2.07)
(812, 'UFC 2009 Undisputed', 'X360', 2009, 'Fighting', 'THQ', 1.48, 0.39, 0.0, 0.19, 2.07)
(813, 'Dark Souls', 'PS3', 2011, 'Role-Playing', 'Namco Bandai Games', 0.75, 0.54, 0.54, 0.23, 2.07)
(814, 'Yu-Gi-Oh! The Eternal Duelist Soul', 'GBA', 2001, 'Strategy', 'Konami Digital Entertainment', 1.64, 0.36, 0.0, 0.07, 2.07)
(815, 'Need for Speed: ProStreet', 'X360', 2007, 'Racing', 'Electronic Arts', 1.04, 0.8, 0.01, 0.22, 2.06)
(816, 'The Sims 3', 'PS3', 2010, 'Simulation', 'Electronic Arts', 0.73, 0.97, 0.02, 0.34, 2.06)
(817, "Tom Clancy's Splinter Cell: Conviction", 'X360', 2010, 'Action', 'Ubisoft', 1.2, 0.63, 0.04, 0.19, 2.06)
(818, 'Pokemon Mystery Dungeon: Red/Blue Rescue Team', 'GBA', 2005, 'Role-Playing', 'Nintendo', 0.71, 0.52, 0.74, 0.08, 2.06)
(819, 'The

(1528, "Yoshi's Woolly World", 'WiiU', 2015, 'Platform', 'Nintendo', 0.61, 0.47, 0.11, 0.1, 1.29)
(1529, 'Mega Man Battle Network 3 Blue / White Version', 'GBA', 2002, 'Role-Playing', 'Capcom', 0.39, 0.02, 0.85, 0.03, 1.29)
(1530, 'FIFA Street', 'PS3', 2012, 'Sports', 'Electronic Arts', 0.11, 0.92, 0.0, 0.25, 1.29)
(1531, 'Resident Evil Zero', 'GC', 2002, 'Action', 'Capcom', 0.54, 0.27, 0.45, 0.04, 1.29)
(1532, 'Need for Speed: Most Wanted', 'X360', 2005, 'Racing', 'Electronic Arts', 1.0, 0.17, 0.02, 0.1, 1.29)
(1533, "Tom Clancy's Rainbow Six: Siege", 'XOne', 2015, 'Shooter', 'Ubisoft', 0.73, 0.44, 0.0, 0.12, 1.29)
(1534, 'Pirates of the Caribbean: The Curse of the Black Pearl', 'GBA', 2003, 'Platform', 'TDK Mediactive', 0.93, 0.34, 0.0, 0.02, 1.29)
(1535, 'Transformers', 'PS2', 2004, 'Shooter', 'Atari', 0.63, 0.49, 0.0, 0.16, 1.29)
(1536, 'Guitar Hero: Aerosmith', 'Wii', 2008, 'Misc', 'Activision', 1.04, 0.14, 0.0, 0.1, 1.29)
(1537, 'Mystery Case Files: MillionHeir', 'DS', 2008, 'Adv

(2148, 'Final Fantasy X / X-2 HD Remaster', 'PSV', 2013, 'Role-Playing', 'Square Enix', 0.21, 0.31, 0.28, 0.16, 0.97)
(2149, 'Medal of Honor: Underground', 'PS', 2000, 'Shooter', 'Electronic Arts', 0.54, 0.37, 0.0, 0.06, 0.97)
(2150, 'The Sims 2', 'DS', 2005, 'Simulation', 'Electronic Arts', 0.82, 0.07, 0.0, 0.07, 0.96)
(2151, 'Dark Cloud 2', 'PS2', 2002, 'Role-Playing', 'Sony Computer Entertainment', 0.38, 0.25, 0.26, 0.07, 0.96)
(2152, "Jampack Summer '99", 'PS', 1999, 'Misc', 'Sony Computer Entertainment', 0.54, 0.36, 0.0, 0.06, 0.96)
(2153, 'PlayStation All-Stars Battle Royale', 'PS3', 2012, 'Action', 'Sony Computer Entertainment', 0.5, 0.28, 0.04, 0.14, 0.96)
(2154, 'Dance Dance Revolution 2nd ReMIX', 'PS', 1999, 'Simulation', 'Konami Digital Entertainment', 0.0, 0.0, 0.9, 0.06, 0.96)
(2155, 'Monster High: Ghoul Spirit', 'DS', 2011, 'Misc', 'THQ', 0.72, 0.17, 0.0, 0.07, 0.96)
(2156, 'Dragon Quest X', 'Wii', 2012, 'Role-Playing', 'Square Enix', 0.0, 0.0, 0.96, 0.0, 0.96)
(2157, 'LE

(2902, 'Spider-Man 2', 'PSP', 2005, 'Action', 'Activision', 0.35, 0.21, 0.0, 0.14, 0.71)
(2903, '2014 FIFA World Cup Brazil', 'PS3', 2014, 'Sports', 'Electronic Arts', 0.15, 0.39, 0.01, 0.16, 0.71)
(2904, 'London 2012: The Official Video Game of the Olympic Games', 'PS3', 2012, 'Sports', 'Sega', 0.06, 0.5, 0.0, 0.15, 0.7)
(2905, 'NHL 12', 'X360', 2011, 'Sports', 'Electronic Arts', 0.55, 0.1, 0.0, 0.05, 0.7)
(2906, "Tony Hawk's Underground", 'GC', 2003, 'Sports', 'Activision', 0.54, 0.14, 0.0, 0.02, 0.7)
(2907, 'Infinite Undiscovery', 'X360', 2008, 'Role-Playing', 'Square Enix', 0.34, 0.18, 0.12, 0.06, 0.7)
(2908, 'Super Bomberman 3', 'SNES', 1994, 'Puzzle', 'Hudson Soft', 0.0, 0.0, 0.7, 0.0, 0.7)
(2909, 'Command & Conquer: Red Alert Retaliation', 'PS', 1998, 'Strategy', 'Virgin Interactive', 0.39, 0.27, 0.0, 0.05, 0.7)
(2910, 'The Sims 2: Apartment Pets', 'DS', 2008, 'Simulation', 'Electronic Arts', 0.32, 0.31, 0.0, 0.07, 0.7)
(2911, 'Star Wars: Obi-Wan', 'XB', 2001, 'Action', 'Activis

...

(13121, 'Winning Post World', 'PS3', 2009, 'Sports', 'Tecmo Koei', 0.0, 0.0, 0.05, 0.0, 0.05)
(13122, 'Arx Fatalis', 'XB', 2003, 'Role-Playing', 'Mindscape', 0.04, 0.01, 0.0, 0.0, 0.05)
(13123, 'Slam Dunk SD Heat Up!!', 'SNES', 1995, 'Sports', 'Namco Bandai Games', 0.0, 0.0, 0.05, 0.0, 0.05)
(13124, 'My Body Coach', 'Wii', 2009, 'Sports', 'Big Ben Interactive', 0.0, 0.04, 0.0, 0.01, 0.05)
(13125, 'Steins;Gate 0', 'PS4', 2015, 'Adventure', 'PQube', 0.0, 0.0, 0.05, 0.0, 0.05)
(13126, 'Adventure Time: Finn & Jake Investigations', 'XOne', 2015, 'Action', 'Little Orbit', 0.02, 0.02, 0.0, 0.0, 0.05)
(13127, 'Dead in the Water', 'PS', 1999, 'Action', 'ASC Games', 0.03, 0.02, 0.0, 0.0, 0.05)
(13128, 'Winning Post 7 2013', 'PS3', 2013, 'Sports', 'Tecmo Koei', 0.0, 0.0, 0.05, 0.0, 0.05)
(13129, 'DiRT 2', 'PC', 2009, 'Racing', 'Codemasters', 0.0, 0.04, 0.0, 0.01, 0.05)
(13130, 'Detective Conan: Prelude from the Past', 'DS', 2012, 'Action', 'Namco Bandai Games', 0.0, 0.0, 0.05, 0.0, 0.05)
(13131, 

(13830, 'Tiger Woods PGA Tour Golf', 'GBA', 2002, 'Sports', 'Ubisoft', 0.03, 0.01, 0.0, 0.0, 0.04)
(13831, 'Twin Strike: Operation Thunder', 'Wii', 2008, 'Shooter', 'Zoo Games', 0.04, 0.0, 0.0, 0.0, 0.04)
(13832, 'BlazBlue: Chrono Phantasma Extend', 'PS3', 2015, 'Action', 'PQube', 0.0, 0.0, 0.04, 0.0, 0.04)
(13833, 'All Points Bulletin', 'PC', 2010, 'Role-Playing', 'Electronic Arts', 0.0, 0.03, 0.0, 0.01, 0.04)
(13834, 'Romance of the Three Kingdoms 13', 'PS3', 2015, 'Action', 'Tecmo Koei', 0.0, 0.0, 0.04, 0.0, 0.04)
(13835, 'The Movies', 'PC', 2005, 'Simulation', 'Activision', 0.01, 0.03, 0.0, 0.01, 0.04)
(13836, 'SuperCar Challenge', 'PS3', 2009, 'Racing', 'System 3 Arcade Software', 0.0, 0.03, 0.0, 0.01, 0.04)
(13837, 'Dreamfall: The Longest Journey', 'XB', 2006, 'Adventure', 'Empire Interactive', 0.03, 0.01, 0.0, 0.0, 0.04)
(13838, 'The Sims 4: Spa Day', 'PC', 2015, 'Simulation', 'Electronic Arts', 0.0, 0.04, 0.0, 0.0, 0.04)
(13839, 'Tokimeki Mahjong Paradise: Koi no Tenpai Beat', 

(14545, "Disney's Aladdin", 'GBA', 2003, 'Platform', 'Capcom', 0.02, 0.01, 0.0, 0.0, 0.03)
(14546, 'Royal Palace of White Sword and The City of Gentiles', 'PC', 2009, 'Role-Playing', 'Take-Two Interactive', 0.0, 0.02, 0.0, 0.01, 0.03)
(14547, 'Virtual Pool: Tournament Edition', 'XB', 2005, 'Sports', 'Global Star', 0.02, 0.01, 0.0, 0.0, 0.03)
(14548, 'Kung Fu Panda: Showdown of Legendary Legends', 'X360', 2015, 'Action', 'Little Orbit', 0.0, 0.03, 0.0, 0.0, 0.03)
(14549, 'Nippon no Asoko de', 'PSP', 2008, 'Misc', 'Sony Computer Entertainment', 0.0, 0.0, 0.03, 0.0, 0.03)
(14550, '007: Quantum of Solace', 'PC', 2008, 'Action', 'Activision', 0.01, 0.01, 0.0, 0.0, 0.03)
(14551, 'MapleStory DS', 'DS', 2010, 'Role-Playing', 'Nexon', 0.0, 0.0, 0.03, 0.0, 0.03)
(14552, 'Phantasy Star Online 2: Episode 3 Deluxe Package', 'PSV', 2015, 'Action', 'Sega', 0.0, 0.0, 0.03, 0.0, 0.03)
(14553, 'Pimp My Ride: Street Racing', 'DS', 2009, 'Racing', 'Activision', 0.03, 0.0, 0.0, 0.0, 0.03)
(14554, "Let's Da

(15356, 'Demolition Company: Gold Edition', 'PC', 2011, 'Simulation', '0', 0.0, 0.02, 0.0, 0.0, 0.02)
(15357, 'Headhunter: Redemption', 'XB', 2004, 'Action', 'Sega', 0.02, 0.0, 0.0, 0.0, 0.02)
(15358, 'Onechanbara Special', 'PSP', 2011, 'Action', 'D3Publisher', 0.0, 0.0, 0.02, 0.0, 0.02)
(15359, 'Daikaijuu Battle: Ultra Coliseum', 'Wii', 2008, 'Fighting', 'Namco Bandai Games', 0.0, 0.0, 0.02, 0.0, 0.02)
(15360, 'Saki: Achiga-Hen Portable', 'PSP', 2013, 'Adventure', 'Alchemist', 0.0, 0.0, 0.02, 0.0, 0.02)
(15361, 'Bella Sara 2 - The Magic of Drasilmare', '3DS', 2013, 'Adventure', 'Big Ben Interactive', 0.0, 0.02, 0.0, 0.0, 0.02)
(15362, 'Minna de Dokusho: Keatai Shousetsu Desu', 'PSP', 2008, 'Misc', 'Dorart', 0.0, 0.0, 0.02, 0.0, 0.02)
(15363, 'Polar Bowler', 'DS', 2008, 'Sports', 'Mumbo Jumbo', 0.02, 0.0, 0.0, 0.0, 0.02)
(15364, 'Prehistorik Man', 'GBA', 2001, 'Platform', 'THQ', 0.01, 0.01, 0.0, 0.0, 0.02)
(15365, 'F1 2002', 'GBA', 2002, 'Racing', 'Destination Software, Inc', 0.01, 0.0

(16274, 'The Humans: Meet the Ancestors!', 'DS', 2009, 'Puzzle', 'Deep Silver', 0.01, 0.0, 0.0, 0.0, 0.01)
(16275, 'Chaos;Head Noah', 'PSV', 2014, 'Adventure', '5pb', 0.0, 0.0, 0.01, 0.0, 0.01)
(16276, 'Battlestations: Midway', 'PC', 2007, 'Strategy', 'Eidos Interactive', 0.0, 0.01, 0.0, 0.0, 0.01)
(16277, 'Farming Simulator 15 Expansion Pack', 'PC', 2015, 'Action', 'Focus Home Interactive', 0.0, 0.01, 0.0, 0.0, 0.01)
(16278, 'Jan Sangoku Musou', 'PS2', 2006, 'Misc', 'Tecmo Koei', 0.0, 0.0, 0.01, 0.0, 0.01)
(16279, 'Assetto Corsa', 'XOne', 2016, 'Racing', '505 Games', 0.0, 0.01, 0.0, 0.0, 0.01)
(16280, 'Kono Aozora ni Yakusoku o: Melody of the Sun and Sea', 'PS2', 2007, 'Adventure', 'Alchemist', 0.0, 0.0, 0.01, 0.0, 0.01)
(16281, 'Monster Bomber', 'DS', 2006, 'Puzzle', '505 Games', 0.01, 0.0, 0.0, 0.0, 0.01)
(16282, 'Rakushou! Pachi-Slot Sengen 6: Rio 2 Cruising Vanadis', 'PS2', 2009, 'Misc', 'Tecmo Koei', 0.0, 0.0, 0.01, 0.0, 0.01)
(16283, 'Fatal Fury: Battle Archives Volume 1 (JP sal